# Выбор локации для скважины

## Описание проекта

Необходимо решить, где бурить новую скважину.

Предоставлены пробы нефти в трёх регионах: в каждом 10 000 месторождений, где измерили качество нефти и объём её запасов. Необходимо построить модель машинного обучения, которая поможет определить регион, где добыча принесёт наибольшую прибыль. 

Шаги для выбора локации:

- В избранном регионе ищут месторождения, для каждого определяют значения признаков;
- Строят модель и оценивают объём запасов;
- Выбирают месторождения с самым высокими оценками значений. Количество месторождений зависит от бюджета компании и стоимости разработки одной скважины;
- Прибыль равна суммарной прибыли отобранных месторождений.

### Цель

Предложить регион для разработки скважин 

### Задачи

1. Загрузить и подготовить данные
2. Обучить и проверить модель для каждого региона
3. Подготовить данные к расчету прибыли
4. Написать функцию для расчета прибыли по выбранным скважинам и предсказаниям модели
5. Посчитать риски и прибыль для каждого региона
6. Выбрать регион

### Описание данных

* id — уникальный идентификатор скважины.
* f0, f1, f2 — три признака точек.
* product — объём запасов в скважине (тыс. баррелей).


### Условия

* Для обучения модели подходит только линейная регрессия (остальные — недостаточно предсказуемые).
* При разведке региона исследуют 500 точек, из которых с помощью машинного обучения выбирают 200 лучших для разработки.
* Бюджет на разработку скважин в регионе — 10 млрд рублей.
* При нынешних ценах один баррель сырья приносит 450 рублей дохода. Доход с каждой единицы продукта составляет 450 тыс. рублей, поскольку объём указан в тысячах баррелей.
* После оценки рисков нужно оставить лишь те регионы, в которых вероятность убытков меньше 2.5%. Среди них выбирают регион с наибольшей средней прибылью.

### Данные геологоразведки

`/datasets/geo_data_0.csv`

`/datasets/geo_data_1.csv`

`/datasets/geo_data_2.csv`

## Загрузка и подготовка данных

In [21]:
!pip install pandas-profiling[notebook,html];


[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [22]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from pandas_profiling import ProfileReport
import numpy as np

Загружаем данные

In [23]:
try:
    data_0 = pd.read_csv('geo_data_0.csv')
    data_1 = pd.read_csv('geo_data_1.csv')
    data_2 = pd.read_csv('geo_data_2.csv')
except:
    data_0 = pd.read_csv('/datasets/geo_data_0.csv')
    data_1 = pd.read_csv('/datasets/geo_data_1.csv')
    data_2 = pd.read_csv('/datasets/geo_data_2.csv')

Изучим данные

**1-й регион**

In [24]:
ProfileReport(data_0)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**2-й регион**

In [25]:
ProfileReport(data_1)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**3-й регион**

In [26]:
ProfileReport(data_2)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Обучение и проверка модели

In [27]:
# функция для получения предсказаний и целевых признаков для валидационной выборки
# также функция выводит средний запас предсказанного сырья в скважине и RMSE.
def get_predictions(data):
    # Разобьем данные на features и targe
    features = data.drop(['id','product'], axis=1)
    target = data['product']
    # Разобьем данные на обучающую и валидационную выборки в соотношении в соотношении 75:25.
    features_train, features_valid, target_train, target_valid = train_test_split(
    features, target, test_size=0.25, random_state=12345)
    # Создадим модели линейной регрессии (остальные-недостаточно предсказуемые)
    model = LinearRegression()
    model.fit(features_train, target_train) # обучим модель
    predictions = model.predict(features_valid) # Сделаем предсказания на валидационной выборке
    print('Средний запас предсказанного сырья в скважине: ', predictions.mean(), 'тыс. баррелей')
    print('RMSE: ', mean_squared_error(predictions, target_valid, squared=False), 'тыс. баррелей')
    return predictions, target_valid 

**1-й регион**

In [28]:
predictions_0, target_valid_0 =  get_predictions(data_0)

Средний запас предсказанного сырья в скважине:  92.59256778438035 тыс. баррелей
RMSE:  37.5794217150813 тыс. баррелей


**2-й регион**

In [29]:
predictions_1, target_valid_1 =  get_predictions(data_1)

Средний запас предсказанного сырья в скважине:  68.72854689544602 тыс. баррелей
RMSE:  0.8930992867756165 тыс. баррелей


**3-й регион**

In [30]:
predictions_2, target_valid_2 =  get_predictions(data_2)

Средний запас предсказанного сырья в скважине:  94.96504596800489 тыс. баррелей
RMSE:  40.02970873393434 тыс. баррелей


В первом и третьем регионах результаты получились похожи. Средние запасы превышают 90 тысяч баррелей. Одноко RMSE для трех регионов получился 
37.58, 0.89 и 40.03, что говорит о низкой точности моделей для 1-го и 2-го регионов.

## Подготовка к расчёту прибыли

Сохраним все ключевые значения в отдельных переменных

In [31]:
EXPLORATORY_WELLS = 500 # в каждом регионе исследуют 500 точек (разведывательные скважины)

In [32]:
PRODUCTION_WELLS = 200 # выбирают 200 наиболее перспективных скважин (добывающие скважины)

In [33]:
EXPENSES = 10*10**9 # расходы на разработку скважин 10 млрд рублей

In [34]:
PRICE = 450_000 # доход с каждой единицы продукта

Расчитаем, сколько должна давать скважина для обеспечения безубыточной работы

In [35]:
EXPENSES/PRODUCTION_WELLS/PRICE

111.11111111111111

Получаем, что при сохранении текущих цен для безубыточной разрабоки скважины достаточно чтобы запасы в ней были не менее 111.11 тысяч баррелей нефти. Средние значения объемов запасов для скважин во всех трех регионах меньше этого порога.

## Расчёт прибыли и рисков 

Функция для расчета прибыли по выбранным скважинам и предсказаниям модели

In [36]:
def revenue(target, predictions, count):
    pred_sorted = predictions.sort_values(ascending=False)
    selected = target[pred_sorted.index][:count]
    return selected.sum() * PRICE - EXPENSES

Применим технику Bootstrap, чтобы найти распределение прибыли

Функция для получения средней прибыли, 95%-го доверительного интервала, и вероятности получить убытки

In [37]:
def get_values(target, predictions, n): # n - число выборок
    state = np.random.RandomState(12345) # для обеспечения воспроизводимости и получения различных случайных выборок
    predictions = pd.Series(predictions) #Для возможности получить доступ к предсказниям через индексы
    predictions.index = target.index # добавляем предсказания соответствующие индексы целеого признака
    values = []
    for i in range(n): # 1000 выборок
        target_sample = target.sample(n=EXPLORATORY_WELLS, replace=True, random_state=state) # случайно выбираем 500 точек
        predictions_sample = predictions[target_sample.index] # смотрим на предсказания для этих точек
        rev = revenue(target_sample, predictions_sample, PRODUCTION_WELLS) # находим даход для полученной выборки
        values.append(rev)
    values = pd.Series(values)
    print('Cредняя прибыль: ', values.mean())
    print('95%-й доверительный интервал')
    print('Нижняя граница доверительного интервала: ', values.quantile(0.025))
    print('Верхняя граница доверительного интервала: ', values.quantile(0.975))
    print('Вероятность получить убытки: ', (values < 0).mean())
    
    

**1-й регион**

In [38]:
get_values(target_valid_0, predictions_0, 1000)

Cредняя прибыль:  425938526.91059244
95%-й доверительный интервал
Нижняя граница доверительного интервала:  -102090094.83793654
Верхняя граница доверительного интервала:  947976353.3583689
Вероятность получить убытки:  0.06


**2-й регион**

In [39]:
get_values(target_valid_1, predictions_1, 1000)

Cредняя прибыль:  515222773.4432899
95%-й доверительный интервал
Нижняя граница доверительного интервала:  68873225.37050176
Верхняя граница доверительного интервала:  931547591.2570494
Вероятность получить убытки:  0.01


**3-й регион**

In [40]:
get_values(target_valid_2, predictions_2, 1000)

Cредняя прибыль:  435008362.7827556
95%-й доверительный интервал
Нижняя граница доверительного интервала:  -128880547.32978901
Верхняя граница доверительного интервала:  969706954.1802661
Вероятность получить убытки:  0.064


В 1-м 3-м регионах риск поучить убытки составляет около 6%, во 2-м регионе этот риск равен 1%. В 1-м и 3-м регионах в 95%-й доверительный интервал входят убытки больше 100  млн., в то время как для 2-го региона в 95%-м доверительном интервале минимальная прибыль равна 68 млн. Кроме того, во 2-м регионе значительно больше средняя прогнозируемая прибыль (515 млн. против 426 млн. и 435 млн.). Иходя из этих соображений, для разработки лучше подходит 2-й регион.